---
format: 
  html:
    toc: false
    page-layout: full
execute:
    echo: false
---

<div class="text-box">

# 2.2 Creating a Folium Map of  Post-secondary buildings per census tracts
    
</div>
    

<div class="text-box">

Here, I'll 
    
1) Use the dataframe from 2.1 to create a folium map of college buildings across Philadelphia clustering the college buildings close to each other for enhanced readability. 
    
2) Create a base map with tool tips of my chosen demographic columns from the "identity_with_tracts" dataframe from part 1, along with three distinct heatmaps that can be toggled between to analyze different demographic trends and how they're spread across Philadelphia in relation to the concentration of college buildings. 
    
</div>

In [3]:
#| echo: false

import altair as alt
import geopandas as gpd
import hvplot
import geopandas as gpd
import pandas as pd
import folium
from folium.plugins import MarkerCluster
from shapely.geometry import Point
import warnings

warnings.filterwarnings("ignore")

In [2]:
#| echo: true
#| code-fold: true


import folium
from folium.plugins import MarkerCluster
import geopandas as gpd
import pandas as pd


tracts_gdf = gpd.read_file("identity_with_tracts.geojson")
buildings_per_tract_gdf = gpd.read_file("buildings_per_tract.geojson")


variables=['Median Household Income',"Associates Degree", 
           "Bachelors Degree or Higher"]



tracts_gdf[variables] = tracts_gdf[variables].apply(
    pd.to_numeric, errors='coerce'
)


buildings_per_tract_gdf['centroid'] = buildings_per_tract_gdf.geometry.centroid


m = folium.Map(location=[39.9526, -75.1652], zoom_start=12)

colors = ['#e6f0ff', '#b3d9ff', '#80bfff', '#4da6ff', '#1a8cff', '#0072ff']

folium.Choropleth(
    geo_data=tracts_gdf,
    name="Bachelors Degree Per Tract",
    data=tracts_gdf,
    columns=["TRACTCE", "Bachelors Degree or Higher"],
    key_on="feature.properties.TRACTCE",
    fill_color="YlGnBu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Bachelors Degree Per Tract"
).add_to(m)


folium.Choropleth(
    geo_data=tracts_gdf,
    name="Associates Degree Per Tract",
    data=tracts_gdf,
    columns=["TRACTCE", "Associates Degree"],
    key_on="feature.properties.TRACTCE",
    fill_color="YlGnBu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Associates Degree Per Tract"
).add_to(m)



folium.Choropleth(
    geo_data=tracts_gdf,
    name="Median Household Income",
    data=tracts_gdf,
    columns=["TRACTCE", "Median Household Income"],
    key_on="feature.properties.TRACTCE",
    fill_color="YlGnBu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Median Household Income Per Tract"
).add_to(m)



folium.GeoJson(
    tracts_gdf,
    style_function=lambda feature: {
        "fillColor": "#2b8cbe",
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.4,
    },
    highlight_function=lambda feature: {
        "weight": 1,
        "color": "yellow",
    },
    tooltip=folium.GeoJsonTooltip(
        fields=[
            "Median Household Income",
            "Hispanic or Latino Total",
            "White and Latino/Hispanic",
            "Black and Latino/Hispanic",
            "Bachelors Degree or Higher",
            "Associates Degree",
            "TRACTCE"
        ],
        aliases=[
            "Median Income:",
            "Total Latino:",
            "White/Latino:",
            "Black/Latino:",
            "Bachelors Degree:",
            "Associates Degree:",
            "tract:"
        ],
        localize=True,
        sticky=False,
        labels=True,
        style="""
            background-color: #F0EFEF;
            border: 2px solid black;
            border-radius: 3px;
            box-shadow: 3px;
        """,
    ),
    name="Base Tracts"
).add_to(m)









marker_cluster = MarkerCluster(name="Buildings").add_to(m)

for idx, row in buildings_per_tract_gdf.iterrows():
    centroid = row['centroid']
    lat, lon = centroid.y, centroid.x

    popup_content = folium.Popup(f"""
        <strong>Name:</strong> {row.get('NAME_left', 'N/A')}<br>
        <strong>Address:</strong> {row.get('ADDRESS', 'N/A')}<br>
        <strong>Description:</strong> {row.get('BUILDING_DESCRIPTION', 'N/A')}<br>
        <strong>Black and Latino/Hispanic:</strong> {row.get('Black and Latino/Hispanic', 'N/A')}<br>
        <strong>Total Population:</strong> {row.get('Total Population', 'N/A')}<br>
        <strong>Median Household Income:</strong> ${row.get('Median Household Income', 'N/A')}<br>
        <strong>Bachelors Degree or Higher:</strong> {row.get('Bachelors Degree or Higher', 'N/A')}<br>
        <strong>Associates Degree:</strong> {row.get('Associates Degree', 'N/A')}<br>
        <strong>Masters Degree:</strong> {row.get('Masters Degree', 'N/A')}<br>
        <strong>White and Latino/Hispanic:</strong> {row.get('White and Latino/Hispanic', 'N/A')}<br>
        <strong>Hispanic or Latino Total:</strong> {row.get('Hispanic or Latino Total', 'N/A')}<br>
    """, max_width=300)

    folium.Marker(
        location=[lat, lon],
        popup=popup_content,
        icon=folium.Icon(color='orange', icon='book')
    ).add_to(marker_cluster)


folium.LayerControl().add_to(m)


m

<div class="text-box">
    
## Analysis

As expected, most buildings are neighboring their campuses, with the heaviest concentration of buildings in the University City Area. However, at first glance, the median household incomes of census tracts containing college buildings are relatively low.  The high concentration of college buildings in lower median household income tracts could be attributred to two causes

1) The adults who are reporting their incomes in  census tracts with college buildings are post-secondary students who do not have a full time job. For example, there is a  relatively high median income of the tracts with a CCP building. CCP is a commuter school in which many students are also part time students who likely have a full time job, and are not living in the area. 

2) The history of gentrification in Philadelphia by post-secondary instiutions. For example, Temple University  has an extensive history of gentrification within lower income neighboorhoods in North Philadelphia, as noted by the lighter blue color scheme within census tracts that have a Temple building when toggling the "Median Household Income" choropleth map in the above folium map. 
    
Moreover, based on the choropleth maps seen in **part 1.2**, the areas that were noted to have heavy Black-Latino, and White-Latino concentrations have little to no college buildings within their census tracts. 

However, my previous rationale is only based off of direct observation of the Folium map. **Part 2.3** will provide an additional analysis of the trends mapped above. 
    
</div>